In [1]:
import pandas as pd
import hvplot.pandas
import numpy as np
from path import Path
import statsmodels.api as sm

In [66]:
# NOTE:
# Data is extracted from
# https://www.tradingview.com/chart/YcV16UR5/?symbol=FX_IDC%3AUSDCNY
# https://www.tradingview.com/chart/YcV16UR5/?symbol=FX_IDC%3AUSDJPY

# For some reason, their is no volume in this dataset under the volume column so I choose to exclude that here.

In [4]:
ICE_USDCNY_1D = Path("Resources/ICE_USDCNY_1D.csv")
ICE_USDJPY_1D = Path("Resources/ICE_USDJPY_1D.csv")

In [5]:
# USD/CNY pair from Tradingview via Intercontinental Exchange (ICE)

In [6]:
usdcny_1D = pd.read_csv(
    ICE_USDCNY_1D,
    index_col="time",
    infer_datetime_format=True,
    parse_dates=True)

/tmp/ipykernel_69730/1249512733.py:1: FutureWarning: The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.
  usdcny_1D = pd.read_csv(


In [7]:
usdcny_1D = usdcny_1D.sort_index()
usdcny_1D = usdcny_1D[["open", "high", "low", "close"]]

usdcny_1D.head(10)

open    high     low   close
time                                      
1981-01-02  1.5341  1.5341  1.5341  1.5341
1981-01-05  1.5418  1.5418  1.5418  1.5418
1981-01-06  1.5264  1.5264  1.5264  1.5264
1981-01-07  1.5264  1.5264  1.5264  1.5264
1981-01-08  1.5264  1.5264  1.5264  1.5264
1981-01-09  1.5371  1.5371  1.5371  1.5371
1981-01-12  1.5371  1.5371  1.5371  1.5371
1981-01-13  1.5449  1.5449  1.5449  1.5449
1981-01-14  1.5449  1.5449  1.5449  1.5449
1981-01-15  1.5449  1.5449  1.5449  1.5449

In [8]:
# Checks to see if their is any missing data
# True = 1 = their is data
# False = 0 = their is no data
usdcny_1D.isna()

open   high    low  close
time                                  
1981-01-02  False  False  False  False
1981-01-05  False  False  False  False
1981-01-06  False  False  False  False
1981-01-07  False  False  False  False
1981-01-08  False  False  False  False
...           ...    ...    ...    ...
2024-03-08  False  False  False  False
2024-03-11  False  False  False  False
2024-03-12  False  False  False  False
2024-03-13  False  False  False  False
2024-03-14  False  False  False  False

[10919 rows x 4 columns]

In [9]:
# There are no missing values here.
usdcny_1D.isna().sum()

open     0
high     0
low      0
close    0
dtype: int64

In [10]:
usdcny_1D_copy = usdcny_1D

In [11]:
# The values this argument can take are specific letters of the alphabet.
# 'h' - hourly
# 'd' - daily
# 'b' - business days
# 'w' - weekly
# 'm' - monthly
# 'a' - annual
usdcny_1D_copy.asfreq('b')

open    high     low   close
time                                      
1981-01-02  1.5341  1.5341  1.5341  1.5341
1981-01-05  1.5418  1.5418  1.5418  1.5418
1981-01-06  1.5264  1.5264  1.5264  1.5264
1981-01-07  1.5264  1.5264  1.5264  1.5264
1981-01-08  1.5264  1.5264  1.5264  1.5264
...            ...     ...     ...     ...
2024-03-08  7.1908  7.1937  7.1836  7.1850
2024-03-11  7.1850  7.1917  7.1807  7.1815
2024-03-12  7.1815  7.1815  7.1717  7.1795
2024-03-13  7.1795  7.1941  7.1795  7.1856
2024-03-14  7.1856  7.1938  7.1856  7.1927

[11270 rows x 4 columns]

In [12]:
# Note:
# I choose 10,20,30 because on average, their is 30 days in a year.
# I wanted to have all those moving average to compare.

# Created a 10-day MA column for usdcny_1D
usdcny_1D_copy['10-day MA'] = usdcny_1D_copy['close'].rolling(window=10).mean()

# Created a 20-day MA column for usdcny_1D
usdcny_1D_copy['20-day MA'] = usdcny_1D_copy['close'].rolling(window=20).mean()

# Created a 30-day MA column for usdcny_1D
usdcny_1D_copy['30-day MA'] = usdcny_1D_copy['close'].rolling(window=30).mean()

usdcny_1D_copy

open    high     low   close  10-day MA  20-day MA  30-day MA
time                                                                       
1981-01-02  1.5341  1.5341  1.5341  1.5341        NaN        NaN        NaN
1981-01-05  1.5418  1.5418  1.5418  1.5418        NaN        NaN        NaN
1981-01-06  1.5264  1.5264  1.5264  1.5264        NaN        NaN        NaN
1981-01-07  1.5264  1.5264  1.5264  1.5264        NaN        NaN        NaN
1981-01-08  1.5264  1.5264  1.5264  1.5264        NaN        NaN        NaN
...            ...     ...     ...     ...        ...        ...        ...
2024-03-08  7.1908  7.1937  7.1836  7.1850    7.19415   7.193385   7.191010
2024-03-11  7.1850  7.1917  7.1807  7.1815    7.19264   7.192840   7.191067
2024-03-12  7.1815  7.1815  7.1717  7.1795    7.19087   7.192195   7.191217
2024-03-13  7.1795  7.1941  7.1795  7.1856    7.18972   7.191855   7.191843
2024-03-14  7.1856  7.1938  7.1856  7.1927    7.19027   7.191870   7.192287

[10919 rows x 7 columns]

In [13]:
# There are a couple missing values here because I'm counting business days and moving average.
usdcny_1D_copy.isna().sum()

open          0
high          0
low           0
close         0
10-day MA     9
20-day MA    19
30-day MA    29
dtype: int64

In [14]:
usdcny_1D_cleaned = usdcny_1D_copy.dropna()

In [15]:
# Checking to see if I have successfully removed the all the empty rows
usdcny_1D_cleaned.isna().sum()

open         0
high         0
low          0
close        0
10-day MA    0
20-day MA    0
30-day MA    0
dtype: int64

In [16]:
usdcny_1D_cleaned.describe()

open          high          low         close     10-day MA  \
count  10890.000000  10890.000000  10890.00000  10890.000000  10890.000000   
mean       6.261072      6.264814      6.25797      6.261067      6.258761   
std        1.989626      1.990759      1.98874      1.989654      1.991392   
min        1.590900      1.590900      1.59090      1.590900      1.606480   
25%        5.433500      5.433500      5.43350      5.433500      5.436253   
50%        6.705400      6.716550      6.69360      6.705450      6.706880   
75%        8.266800      8.267000      8.26680      8.266900      8.267437   
max        8.740900      8.740900      8.74090      8.740900      8.730800   

          20-day MA     30-day MA  
count  10890.000000  10890.000000  
mean       6.256185      6.253599  
std        1.993374      1.995370  
min        1.584985      1.568790  
25%        5.439689      5.433186  
50%        6.706480      6.708648  
75%        8.267569      8.267537  
max        8.726595      8.726090

In [17]:
usdcny_1D_cleaned.head()

open    high     low   close  10-day MA  20-day MA  30-day MA
time                                                                       
1981-02-13  1.6285  1.6285  1.6285  1.6285    1.60648   1.584985   1.568790
1981-02-17  1.6579  1.6579  1.6579  1.6579    1.61341   1.590095   1.572917
1981-02-18  1.6298  1.6298  1.6298  1.6298    1.61531   1.593800   1.575850
1981-02-19  1.6298  1.6298  1.6298  1.6298    1.61721   1.597505   1.579297
1981-02-20  1.6021  1.6021  1.6021  1.6021    1.61714   1.599825   1.581820

In [18]:
usdcny_1D_cleaned_hvplot = usdcny_1D_cleaned.hvplot(title="USD/CNY")
usdcny_1D_cleaned_hvplot

:NdOverlay   [Variable]
   :Curve   [time]   (value)

In [19]:
# USD/JPY pair from Tradingview via Intercontinental Exchange (ICE)

In [20]:
usdjpy_1D = pd.read_csv(
    ICE_USDJPY_1D,
    index_col="time",
    infer_datetime_format=True,
    parse_dates=True)

/tmp/ipykernel_69730/2093499537.py:1: FutureWarning: The argument 'infer_datetime_format' is deprecated and will be removed in a future version. A strict version of it is now the default, see https://pandas.pydata.org/pdeps/0004-consistent-to-datetime-parsing.html. You can safely remove this argument.
  usdjpy_1D = pd.read_csv(


In [21]:
usdjpy_1D = usdjpy_1D.sort_index()
usdjpy_1D = usdjpy_1D[["open", "high", "low", "close"]]

usdjpy_1D.head(10)

open    high     low   close
time                                      
1980-09-09  216.50  216.50  216.50  216.50
1980-09-10  216.59  216.59  216.59  216.59
1980-09-11  214.22  214.22  214.22  214.22
1980-09-12  212.70  212.70  212.70  212.70
1980-09-15  212.65  212.65  212.65  212.65
1980-09-16  211.55  211.55  211.55  211.55
1980-09-17  211.65  211.65  211.65  211.65
1980-09-18  212.95  212.95  212.95  212.95
1980-09-19  210.95  210.95  210.95  210.95
1980-09-22  214.90  214.90  214.90  214.90

In [22]:
# Checks to see if their is any missing data
# True = 1 = their is data
# False = 0 = their is no data
usdjpy_1D.isna()

open   high    low  close
time                                  
1980-09-09  False  False  False  False
1980-09-10  False  False  False  False
1980-09-11  False  False  False  False
1980-09-12  False  False  False  False
1980-09-15  False  False  False  False
...           ...    ...    ...    ...
2024-03-11  False  False  False  False
2024-03-12  False  False  False  False
2024-03-13  False  False  False  False
2024-03-14  False  False  False  False
2024-03-15  False  False  False  False

[11271 rows x 4 columns]

In [23]:
# There are no missing values here.
usdjpy_1D.isna().sum()

open     0
high     0
low      0
close    0
dtype: int64

In [24]:
usdjpy_1D_copy = usdjpy_1D

In [25]:
# The values this argument can take are specific letters of the alphabet.
# 'h' - hourly
# 'd' - daily
# 'b' - business days
# 'w' - weekly
# 'm' - monthly
# 'a' - annual
usdjpy_1D_copy.asfreq('b')

open     high      low    close
time                                          
1980-09-09  216.500  216.500  216.500  216.500
1980-09-10  216.590  216.590  216.590  216.590
1980-09-11  214.220  214.220  214.220  214.220
1980-09-12  212.700  212.700  212.700  212.700
1980-09-15  212.650  212.650  212.650  212.650
...             ...      ...      ...      ...
2024-03-11  147.020  147.147  146.489  146.965
2024-03-12  146.951  148.186  146.625  147.610
2024-03-13  147.610  148.050  147.236  147.624
2024-03-14  147.624  148.358  147.439  148.260
2024-03-15  148.280  148.290  148.230  148.243

[11354 rows x 4 columns]

In [26]:
# Note:
# I choose 10,20,30 because on average, their is 30 days in a year.
# I wanted to have all those moving average to compare.

# Created a 10-day MA column for usdcny_1D
usdjpy_1D_copy['10-day MA'] = usdjpy_1D_copy['close'].rolling(window=10).mean()

# Created a 20-day MA column for usdcny_1D
usdjpy_1D_copy['20-day MA'] = usdjpy_1D_copy['close'].rolling(window=20).mean()

# Created a 30-day MA column for usdcny_1D
usdjpy_1D_copy['30-day MA'] = usdjpy_1D_copy['close'].rolling(window=30).mean()

usdjpy_1D_copy

open     high      low    close  10-day MA  20-day MA  \
time                                                                   
1980-09-09  216.500  216.500  216.500  216.500        NaN        NaN   
1980-09-10  216.590  216.590  216.590  216.590        NaN        NaN   
1980-09-11  214.220  214.220  214.220  214.220        NaN        NaN   
1980-09-12  212.700  212.700  212.700  212.700        NaN        NaN   
1980-09-15  212.650  212.650  212.650  212.650        NaN        NaN   
...             ...      ...      ...      ...        ...        ...   
2024-03-11  147.020  147.147  146.489  146.965   149.3066  149.82255   
2024-03-12  146.951  148.186  146.625  147.610   149.0188  149.66270   
2024-03-13  147.610  148.050  147.236  147.624   148.7140  149.51720   
2024-03-14  147.624  148.358  147.439  148.260   148.5452  149.43545   
2024-03-15  148.280  148.290  148.230  148.243   148.3631  149.33855   

             30-day MA  
time                    
1980-09-09         NaN  
1980-09-10         NaN  
1980-09-11         NaN  
1980-09-12         NaN  
1980-09-15         NaN  
...                ...  
2024-03-11  149.276167  
2024-03-12  149.276533  
2024-03-13  149.302100  
2024-03-14  149.364200  
2024-03-15  149.362033  

[11271 rows x 7 columns]

In [27]:
# There are a couple missing values here because I'm counting business days and moving average.
usdjpy_1D_copy.isna().sum()

open          0
high          0
low           0
close         0
10-day MA     9
20-day MA    19
30-day MA    29
dtype: int64

In [28]:
usdjpy_1D_cleaned = usdjpy_1D_copy.dropna()

In [29]:
# Checking to see if I have successfully removed the all the empty rows
usdjpy_1D_cleaned.isna().sum()

open         0
high         0
low          0
close        0
10-day MA    0
20-day MA    0
30-day MA    0
dtype: int64

In [30]:
usdjpy_1D_cleaned.describe()

open          high          low         close     10-day MA  \
count  11242.000000  11242.000000  11242.00000  11242.000000  11242.000000   
mean     129.524280    129.998678    129.03249    129.519241    129.543229   
std       42.745192     42.617848     42.86863     42.739255     42.750502   
min       75.580000     76.000000     75.57500     75.812000     76.367900   
25%      106.208500    106.726500    105.77000    106.220000    106.256250   
50%      116.395000    117.044000    115.79000    116.397500    116.603000   
75%      134.350000    134.916000    133.63650    134.300000    134.167750   
max      277.650000    277.650000    277.65000    277.650000    276.593000   

          20-day MA     30-day MA  
count  11242.000000  11242.000000  
mean     129.569751    129.597279  
std       42.763537     42.777878  
min       76.597750     76.589833  
25%      106.370250    106.527925  
50%      116.609875    116.578183  
75%      134.245125    134.015500  
max      273.667000    271.937333

In [31]:
usdjpy_1D_cleaned.head()

open    high     low   close  10-day MA  20-day MA   30-day MA
time                                                                        
1980-10-20  208.48  208.48  208.48  208.48    208.075   209.7595  210.995000
1980-10-21  208.00  208.00  208.00  208.00    207.980   209.2845  210.711667
1980-10-22  209.40  209.40  209.40  209.40    208.079   208.9845  210.472000
1980-10-23  210.45  210.45  210.45  210.45    208.229   208.8035  210.346333
1980-10-24  212.42  212.42  212.42  212.42    208.596   208.8010  210.337000

In [32]:
usdjpy_1D_cleaned_hvplot = usdjpy_1D_cleaned.hvplot(title="USD/JPY")
usdjpy_1D_cleaned_hvplot

:NdOverlay   [Variable]
   :Curve   [time]   (value)

In [62]:
# In 1985, the Plaza Accord Agreement happened which is probably what drove the changes you see with the currencies.
# https://www.youtube.com/watch?v=splYJ2HICBk

# As we're trying to complete this project, I realize their are many important dates here, but it's going to be hard to include them all here so I decided to create this code below to easily compare the charts by year >>>

In [63]:
# Change year to make the comparsion below
year = "1985"

In [64]:
# Refresh this cell after entering the year above to execute latest update
usdcny_1D_cleaned.loc[year].hvplot(title = f"USD/CNY in the year ({year})")

:NdOverlay   [Variable]
   :Curve   [time]   (value)

In [65]:
# Refresh this cell after entering the year above to execute latest update
usdjpy_1D_cleaned.loc[year].hvplot(title = f"USD/JPY in the year ({year})")

:NdOverlay   [Variable]
   :Curve   [time]   (value)

In [36]:
# Is this the bottom information really needed???
# If so, we need to fix this..

In [37]:
# Concatenate the DataFrames
concatenated_df = pd.concat([usdcny_1D_cleaned, usdjpy_1D_cleaned], axis=1)

# Making sure that the concatenation is easily identifiable
concatenated_df.columns = pd.MultiIndex.from_tuples([('usdcny', col) for col in usdcny_1D_cleaned.columns] + [('usdjpy', col) for col in usdjpy_1D_cleaned.columns])

In [38]:
concatenated_df_copy = concatenated_df

In [39]:
# There are a couple missing values here because I'm counting business days and moving average.
concatenated_df_copy.isna().sum()

usdcny  open         370
        high         370
        low          370
        close        370
        10-day MA    370
        20-day MA    370
        30-day MA    370
usdjpy  open          18
        high          18
        low           18
        close         18
        10-day MA     18
        20-day MA     18
        30-day MA     18
dtype: int64

In [40]:
concatenated_df_cleaned = concatenated_df_copy.dropna()

In [41]:
# Checking to see if I have successfully removed the all the empty rows
concatenated_df_cleaned.isna().sum()

usdcny  open         0
        high         0
        low          0
        close        0
        10-day MA    0
        20-day MA    0
        30-day MA    0
usdjpy  open         0
        high         0
        low          0
        close        0
        10-day MA    0
        20-day MA    0
        30-day MA    0
dtype: int64

In [42]:
concatenated_df_cleaned.describe()

usdcny                                                          \
               open          high           low         close     10-day MA   
count  10872.000000  10872.000000  10872.000000  10872.000000  10872.000000   
mean       6.266325      6.270072      6.263218      6.266319      6.264048   
std        1.985818      1.986945      1.984936      1.985846      1.987561   
min        1.590900      1.590900      1.590900      1.590900      1.606480   
25%        5.447625      5.447625      5.447625      5.447625      5.442172   
50%        6.707050      6.718050      6.696200      6.707900      6.708365   
75%        8.266800      8.267000      8.266800      8.266900      8.267495   
max        8.740900      8.740900      8.740900      8.740900      8.730800   

                                         usdjpy                              \
          20-day MA     30-day MA          open          high           low   
count  10872.000000  10872.000000  10872.000000  10872.000000  10872.000000   
mean       6.261499      6.258925    129.026017    129.502851    128.530672   
std        1.989517      1.991503     42.688004     42.564718     42.808145   
min        1.584985      1.568790     75.580000     76.000000     75.575000   
25%        5.443690      5.442057    106.058750    106.549000    105.580000   
50%        6.709632      6.710838    115.875000    116.490000    115.340000   
75%        8.267616      8.267540    134.000000    134.612500    133.350000   
max        8.726595      8.726090    277.650000    277.650000    277.650000   

                                                               
              close     10-day MA     20-day MA     30-day MA  
count  10872.000000  10872.000000  10872.000000  10872.000000  
mean     129.020532    129.040974    129.065897    129.088620  
std       42.682811     42.690425     42.701989     42.711160  
min       75.812000     76.367900     76.597750     76.589833  
25%      106.058750    106.097725    106.194862    106.378333  
50%      115.890000    116.006500    116.050750    115.967167  
75%      133.975000    133.786975    133.717425    133.577500  
max      277.650000    276.593000    273.667000    271.937333

In [50]:
# How do I convert this to a heatmap and is this even correct????

In [ ]:
# haven't figured this part out yet..

# Example: Fit an ARIMA model
model = sm.tsa.ARIMA("??????", order=(p, d, q))  # Replace p, d, q with appropriate values
results = model.fit()
print(results.summary())